<a href="https://colab.research.google.com/github/melzismn/LearningOn3Dgeometries/blob/master/PointNet_Demo.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [1]:
import torch
import plotly
import numpy as np

import plotly.graph_objects as go

# Utilities functions

In [2]:
from typing import Union
from plotly.graph_objs import Layout

from typing import Union, Sequence, Optional
from plotly.graph_objs import Layout
from plotly.subplots import make_subplots


def plot3d(
    x: Union[np.ndarray, torch.Tensor], c: Union[np.ndarray, torch.Tensor]
) -> None:
    """
    Plot the function c over the point cloud x
    """
    fig = go.Figure(
        data=[
            go.Scatter3d(
                x=x[:, 0],
                y=x[:, 1],
                z=x[:, 2],
                mode="markers",
                marker=dict(color=c, colorscale="viridis", size=5, showscale=True),
            )
        ],
        layout=Layout(scene=dict(aspectmode="data")),
    )
    fig.show()
  
def plot3d_shapes(
    x: Sequence[Union[np.ndarray, torch.Tensor]], c: Sequence[Union[np.ndarray, torch.Tensor]], subplot_titles: Optional[Sequence[str]] = None
) -> None:
    """
    Plot the function c over the point cloud x
    """
    fig = make_subplots(
        rows=1,
        cols=len(x),
        specs=[[{"is_3d": True}] * len(x)],
        horizontal_spacing=0,
        vertical_spacing=0,
        subplot_titles=subplot_titles if subplot_titles is not None else None,

    )

    myscene = dict(
        camera=dict(
            up=dict(x=0, y=1, z=0),
            center=dict(x=0, y=0, z=0),
            eye=dict(x=-0.25, y=0.25, z=2.75),
        ),
        aspectmode="data",
    )

    for i, (points, color) in enumerate(zip(x, c)):
      fig.add_trace(
          go.Scatter3d(
                x=points[:, 0],
                y=points[:, 1],
                z=points[:, 2],
                mode="markers",
                marker=dict(color=color, colorscale="viridis", size=5, showscale=True),
            ),
            row=1,
            col=i+1
      )
    
    for i in range(len(x)):
      fig["layout"][f"scene{i+1}"].update(myscene)
    
    fig.update_layout(margin=dict(l=0, r=0, b=0, t=30))

    fig.show()

# Download data

In [3]:
!wget -O 'data.zip' "https://www.dropbox.com/sh/qzh9bo3rbpd0k7d/AAA_dUzVFHBBqLrS8qslYCMJa?dl=1"

--2021-09-22 09:15:34--  https://www.dropbox.com/sh/qzh9bo3rbpd0k7d/AAA_dUzVFHBBqLrS8qslYCMJa?dl=1
Resolving www.dropbox.com (www.dropbox.com)... 162.125.3.18, 2620:100:601b:18::a27d:812
Connecting to www.dropbox.com (www.dropbox.com)|162.125.3.18|:443... connected.
HTTP request sent, awaiting response... 301 Moved Permanently
Location: /sh/dl/qzh9bo3rbpd0k7d/AAA_dUzVFHBBqLrS8qslYCMJa [following]
--2021-09-22 09:15:34--  https://www.dropbox.com/sh/dl/qzh9bo3rbpd0k7d/AAA_dUzVFHBBqLrS8qslYCMJa
Reusing existing connection to www.dropbox.com:443.
HTTP request sent, awaiting response... 302 Found
Location: https://uca01085a0b8c7a264047a22f3f2.dl.dropboxusercontent.com/zip_download_get/A6A2u3ami8f8puwsCFABTw4gDrgQsy2O-znNXrsYXQ4x-HhNcL0_4jlexyLKF7uarY3A9d4Zq5RYYWWt3Bq6MDhUritu8Wm6vhG6V_bpWz5Kpw?dl=1# [following]
--2021-09-22 09:15:35--  https://uca01085a0b8c7a264047a22f3f2.dl.dropboxusercontent.com/zip_download_get/A6A2u3ami8f8puwsCFABTw4gDrgQsy2O-znNXrsYXQ4x-HhNcL0_4jlexyLKF7uarY3A9d4Zq5RYY

In [4]:
!unzip data.zip

Archive:  data.zip
mapname:  conversion of  failed
 extracting: template1K.obj          
 extracting: 12k_shapes_test.npy     
 extracting: 200_shapes_test.npy     
 extracting: 2K_shapes_train.npy     
 extracting: 12k_shapes_train.npy    
 extracting: head_idxs4template1K.txt  
 extracting: belly_idxs4template1K.txt  


In [5]:
!ls

12k_shapes_test.npy   2K_shapes_train.npy	 head_idxs4template1K.txt
12k_shapes_train.npy  belly_idxs4template1K.txt  sample_data
200_shapes_test.npy   data.zip			 template1K.obj


# Setup data pipeline 

In [6]:
from torch.utils.data import Dataset

In [7]:
from typing import Dict

class ShapeLocalizationDataset(Dataset):
  def __init__(self, shapes_data_name: str , region_data_name: str):
    super().__init__()
    self.shapes_data_name = shapes_data_name
    self.region_data_name = region_data_name

    self.shapes = np.load(shapes_data_name).astype(np.float32)

    self.region_idxs = np.loadtxt(region_data_name).astype(np.int64) - 1 
    self.mask = np.zeros(self.shapes.shape[1], dtype=np.int64)
    self.mask[self.region_idxs] = 1
  
  def __len__(self) -> int:
    return self.shapes.shape[0]
  
  def __getitem__(self, idx: int) -> Dict[str, np.ndarray]:
    """ Returns the points of a point cloud with shape [n, 3] and the region 
    that must be localized with shape [n]
    """
    shape = self.shapes[idx]
    return {
        'id': idx,
        'points': shape,
        'mask': self.mask
    }
  
  def __repr__(self):
    return f"ShapeLocalizationDataset(shapes_data_name='{self.shapes_data_name}', region_data_name='{self.region_data_name}')"

In [8]:
print(ShapeLocalizationDataset('2K_shapes_train.npy', 'belly_idxs4template1K.txt'))

ShapeLocalizationDataset(shapes_data_name='2K_shapes_train.npy', region_data_name='belly_idxs4template1K.txt')


In [10]:
#@title Explore data { run: "auto" }
shapes_data = "12k_shapes_train.npy" #@param ["12k_shapes_test.npy", "2K_shapes_train.npy", "12k_shapes_train.npy", "200_shapes_test.npy"]
region_data = "belly_idxs4template1K.txt" #@param ["head_idxs4template1K.txt", "belly_idxs4template1K.txt"]
sample_idx = 27 #@param {type:"slider", min:0, max:100, step:1}


dataset = ShapeLocalizationDataset(shapes_data_name=shapes_data, region_data_name=region_data)

sample = dataset[sample_idx]
plot3d(sample['points'], sample['mask'])

# Setup data loaders

In [11]:
from torch.utils.data import DataLoader

In [12]:
# Decide with data to use
shapes_data_train = "12k_shapes_train.npy"
shapes_data_test = "12k_shapes_test.npy"
region_data = "belly_idxs4template1K.txt"

In [13]:
train_dataset = ShapeLocalizationDataset(shapes_data_name=shapes_data_train, region_data_name=region_data)
test_dataset = ShapeLocalizationDataset(shapes_data_name=shapes_data_test, region_data_name=region_data)

In [14]:
# Hyperparameters

batch_size = 16
num_workers = 2  # number of parallel processes to use to prepare batches

In [15]:
train_dataloader = DataLoader(train_dataset, batch_size=batch_size, num_workers=num_workers, pin_memory=True)
test_dataloader = DataLoader(test_dataset, batch_size=batch_size, num_workers=num_workers, pin_memory=True)

In [16]:
for batch in train_dataloader:
  print(batch)
  break

{'id': tensor([ 0,  1,  2,  3,  4,  5,  6,  7,  8,  9, 10, 11, 12, 13, 14, 15]), 'points': tensor([[[ 1.6780e-01, -4.6215e-01,  4.3317e-01],
         [ 1.6511e-01, -4.6218e-01,  4.3140e-01],
         [ 1.6573e-01, -4.6218e-01,  4.3889e-01],
         ...,
         [ 1.0720e-01, -5.2767e-01,  8.9279e-02],
         [ 1.1388e-01, -5.3017e-01,  8.3889e-02],
         [ 1.1666e-01, -5.2628e-01,  8.6723e-02]],

        [[ 1.2757e-01, -3.7390e-01, -1.9003e-01],
         [ 1.2679e-01, -3.7165e-01, -1.9190e-01],
         [ 1.2736e-01, -3.7170e-01, -1.8485e-01],
         ...,
         [-1.9502e-01, -2.6664e-02, -1.9947e-01],
         [-2.0010e-01, -3.3701e-02, -2.0198e-01],
         [-2.0096e-01, -2.9526e-02, -2.0579e-01]],

        [[-3.3162e-02, -9.1667e-02,  4.1214e-01],
         [-3.1327e-02, -9.0591e-02,  4.1016e-01],
         [-3.3932e-02, -9.7003e-02,  4.1106e-01],
         ...,
         [-3.5983e-02, -8.4408e-02,  3.9471e-01],
         [-2.8670e-02, -8.5113e-02,  3.9959e-01],
         [-3.

# Model definition: PyTorch Lightning

![](https://github.com/PyTorchLightning/pytorch-lightning/raw/master/docs/source/_static/images/general/pl_quick_start_full_compressed.gif)

In [17]:
! pip install pytorch-lightning

     |████████████████████████████████| 923 kB 5.2 MB/s 
     |████████████████████████████████| 282 kB 43.1 MB/s 
     |████████████████████████████████| 636 kB 41.4 MB/s 
     |████████████████████████████████| 119 kB 46.1 MB/s 
     |████████████████████████████████| 829 kB 37.7 MB/s 
     |████████████████████████████████| 1.3 MB 24.0 MB/s 
     |████████████████████████████████| 142 kB 55.5 MB/s 
     |████████████████████████████████| 294 kB 41.2 MB/s 
  Created wheel for future: filename=future-0.18.2-py3-none-any.whl size=491070 sha256=03a574f327898fb9ceef6cee41569420d2e894018e47a0edbc2b24ece03d1211
  Stored in directory: /root/.cache/pip/wheels/56/b0/fe/4410d17b32f1f0c3cf54cdfb2bc04d7b4b8f4ae377e2229ba0
Successfully built future
  Attempting uninstall: PyYAML
    Found existing installation: PyYAML 3.13
    Uninstalling PyYAML-3.13:
      Successfully uninstalled PyYAML-3.13
  Attempting uninstall: future
    Found existing installation: future 0.16.0
    Uninstalling future-0

In [18]:
import pytorch_lightning as pl
from torch import nn

In [19]:
import torch
import torch.nn as nn
import torch.nn.parallel
import torch.utils.data
from torch.autograd import Variable
import numpy as np
import torch.nn.functional as F


class STN3d(nn.Module):
    def __init__(self):
        super(STN3d, self).__init__()
        self.conv1 = torch.nn.Conv1d(3, 64, 1)
        self.conv2 = torch.nn.Conv1d(64, 128, 1)
        self.conv3 = torch.nn.Conv1d(128, 1024, 1)
        self.fc1 = nn.Linear(1024, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, 9)
        self.relu = nn.ReLU()

        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)
        self.bn4 = nn.BatchNorm1d(512)
        self.bn5 = nn.BatchNorm1d(256)


    def forward(self, x):
        batchsize = x.size()[0]
        x = F.relu(self.bn1(self.conv1(x)))
        x = F.relu(self.bn2(self.conv2(x)))
        x = F.relu(self.bn3(self.conv3(x)))
        x = torch.max(x, 2, keepdim=True)[0]
        x = x.view(-1, 1024)

        x = F.relu(self.bn4(self.fc1(x)))
        x = F.relu(self.bn5(self.fc2(x)))
        x = self.fc3(x)

        iden = Variable(torch.from_numpy(np.array([1,0,0,0,1,0,0,0,1]).astype(np.float32))).view(1,9).repeat(batchsize,1)
        if x.is_cuda:
            iden = iden.cuda()
        x = x + iden
        x = x.view(-1, 3, 3)
        return x


class STNkd(nn.Module):
    def __init__(self, k=64):
        super(STNkd, self).__init__()
        self.conv1 = torch.nn.Conv1d(k, 64, 1)
        self.conv2 = torch.nn.Conv1d(64, 128, 1)
        self.conv3 = torch.nn.Conv1d(128, 1024, 1)
        self.fc1 = nn.Linear(1024, 512)
        self.fc2 = nn.Linear(512, 256)
        self.fc3 = nn.Linear(256, k*k)
        self.relu = nn.ReLU()

        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)
        self.bn4 = nn.BatchNorm1d(512)
        self.bn5 = nn.BatchNorm1d(256)

        self.k = k

    def forward(self, x):
        batchsize = x.size()[0]
        x = F.relu(self.bn1(self.conv1(x)))
        x = F.relu(self.bn2(self.conv2(x)))
        x = F.relu(self.bn3(self.conv3(x)))
        x = torch.max(x, 2, keepdim=True)[0]
        x = x.view(-1, 1024)

        x = F.relu(self.bn4(self.fc1(x)))
        x = F.relu(self.bn5(self.fc2(x)))
        x = self.fc3(x)

        iden = Variable(torch.from_numpy(np.eye(self.k).flatten().astype(np.float32))).view(1,self.k*self.k).repeat(batchsize,1)
        if x.is_cuda:
            iden = iden.cuda()
        x = x + iden
        x = x.view(-1, self.k, self.k)
        return x

class PointNetfeat(nn.Module):
    def __init__(self, global_feat = True, feature_transform = False):
        super(PointNetfeat, self).__init__()
        self.stn = STN3d()
        self.conv1 = torch.nn.Conv1d(3, 64, 1)
        self.conv2 = torch.nn.Conv1d(64, 128, 1)
        self.conv3 = torch.nn.Conv1d(128, 1024, 1)
        self.bn1 = nn.BatchNorm1d(64)
        self.bn2 = nn.BatchNorm1d(128)
        self.bn3 = nn.BatchNorm1d(1024)
        self.global_feat = global_feat
        self.feature_transform = feature_transform
        if self.feature_transform:
            self.fstn = STNkd(k=64)

    def forward(self, x):
        n_pts = x.size()[2]
        trans = self.stn(x)
        x = x.transpose(2, 1)
        x = torch.bmm(x, trans)
        x = x.transpose(2, 1)
        x = F.relu(self.bn1(self.conv1(x)))

        if self.feature_transform:
            trans_feat = self.fstn(x)
            x = x.transpose(2,1)
            x = torch.bmm(x, trans_feat)
            x = x.transpose(2,1)
        else:
            trans_feat = None

        pointfeat = x
        x = F.relu(self.bn2(self.conv2(x)))
        x = self.bn3(self.conv3(x))
        x = torch.max(x, 2, keepdim=True)[0]
        x = x.view(-1, 1024)
        if self.global_feat:
            return x, trans, trans_feat
        else:
            x = x.view(-1, 1024, 1).repeat(1, 1, n_pts)
            return torch.cat([x, pointfeat], 1), trans, trans_feat


class PointNetDenseCls(nn.Module):
    def __init__(self, k = 2, feature_transform=False):
        super(PointNetDenseCls, self).__init__()
        self.k = k
        self.feature_transform=feature_transform
        self.feat = PointNetfeat(global_feat=False, feature_transform=feature_transform)
        self.conv1 = torch.nn.Conv1d(1088, 512, 1)
        self.conv2 = torch.nn.Conv1d(512, 256, 1)
        self.conv3 = torch.nn.Conv1d(256, 128, 1)
        self.conv4 = torch.nn.Conv1d(128, self.k, 1)
        self.bn1 = nn.BatchNorm1d(512)
        self.bn2 = nn.BatchNorm1d(256)
        self.bn3 = nn.BatchNorm1d(128)

    def forward(self, x):
        batchsize = x.size()[0]
        n_pts = x.size()[2]
        x, trans, trans_feat = self.feat(x)
        x = F.relu(self.bn1(self.conv1(x)))
        x = F.relu(self.bn2(self.conv2(x)))
        x = F.relu(self.bn3(self.conv3(x)))
        x = self.conv4(x)
        x = x.transpose(2,1).contiguous()
        x = F.log_softmax(x.view(-1,self.k), dim=-1)  # do not use crossentropy
        x = x.view(batchsize, n_pts, self.k)
        return x, trans, trans_feat

In [20]:
! pip install torchmetrics

In [21]:
from torch.nn.functional import nll_loss
import torchmetrics

class RegionLocalizationModule(pl.LightningModule):
  def __init__(self):
    super().__init__()

    self.pointnet = PointNetDenseCls(k=2, feature_transform=True)

    self.train_accuracy = torchmetrics.Accuracy()
    self.test_accuracy = torchmetrics.Accuracy()

  def forward(self, points: torch.Tensor) -> torch.Tensor:
    """
    Defines the behaviour in the forward pass

    Args:
      points: shape points with shape [batch, xyz, num_points]

    Returns:
      probability distributions over the classes for each point [batch, xyz, k]
    """
    points = points.transpose(1, 2)
    out, _, _ = self.pointnet(points)
    return out

  def training_step(self, batch, batch_idx):
    """
    Defines the training logic
    """
    points = batch['points']
    y = batch['mask']

    y_pred = self(points)


    y_pred = y_pred.transpose(1, 2)
    loss = nll_loss(y_pred, y)

    self.train_accuracy(y_pred.exp(), y)

    self.log_dict({'train_loss': loss, 'train_acc': self.train_accuracy}, on_step=True, on_epoch=True, prog_bar=True)

    return loss
  

  def test_step(self, batch, batch_idx):
    """
    Defines the training logic
    """
    points = batch['points']
    y = batch['mask']

    y_pred = self(points)


    y_pred = y_pred.transpose(1, 2)
    loss = nll_loss(y_pred, y)

    self.test_accuracy(y_pred.exp(), y)

    self.log_dict({'test_loss': loss, 'test_acc': self.test_accuracy}, on_epoch=True, prog_bar=True)

    return loss

  def configure_optimizers(self):
    """
    Configure optimizers
    """
    return torch.optim.AdamW(self.parameters())

# Train the model

In [22]:
# Instantiate the model
model = RegionLocalizationModule()

In [23]:
# Instantiate the trainer
trainer = pl.Trainer(gpus=1, max_steps=8000, max_epochs=100)

GPU available: True, used: True
TPU available: False, using: 0 TPU cores
IPU available: False, using: 0 IPUs


In [24]:
results = trainer.test(model, test_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]


Testing: 0it [00:00, ?it/s]

--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9580000042915344, 'test_loss': 0.6410543918609619}
--------------------------------------------------------------------------------


In [25]:
# Train the model
trainer.fit(model, train_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]

  | Name           | Type             | Params
----------------------------------------------------
0 | pointnet       | PointNetDenseCls | 3.5 M 
1 | train_accuracy | Accuracy         | 0     
2 | test_accuracy  | Accuracy         | 0     
----------------------------------------------------
3.5 M     Trainable params
0         Non-trainable params
3.5 M     Total params
14.109    Total estimated model params size (MB)


Training: -1it [00:00, ?it/s]

In [ ]:
results = trainer.test(model, test_dataloader)

LOCAL_RANK: 0 - CUDA_VISIBLE_DEVICES: [0]



--------------------------------------------------------------------------------
DATALOADER:0 TEST RESULTS
{'test_acc': 0.9754753708839417, 'test_loss': 0.0571284256875515}
--------------------------------------------------------------------------------


In [ ]:
#@title Explore predictions { run: "auto" }
shapes_data = "12k_shapes_test.npy" #@param ["12k_shapes_test.npy", "200_shapes_test.npy"]
region_data = "belly_idxs4template1K.txt" #@param ["head_idxs4template1K.txt", "belly_idxs4template1K.txt"]
dataset = ShapeLocalizationDataset(shapes_data_name=shapes_data, region_data_name=region_data)

sample_idx = 592 #@param {type:"slider", min:0, max:1000, step:1}
permute_points = True #@param {type:"boolean"}
sample_points = False #@param {type:"boolean"}
number_of_sampled_points = 274 #@param {type:"slider", min:5, max:1000, step:1}

model = model.cpu()
model.eval()

if sample_idx > len(dataset):
  print(f'Sample idx over the selected dataset length. Setted to : {len(dataset)}')
  sample_idx = len(dataset) - 1

# [1, n_points, xyz]
points = torch.from_numpy(dataset[sample_idx]['points'])[None, ...]

y = dataset[sample_idx]['mask']


if permute_points:
  perm_points = torch.randperm(1000)
  points = points[:, perm_points, :]
  y = y[perm_points]

if sample_points:
  points_to_keep = torch.randperm(1000)[:number_of_sampled_points]
  points = points[:, points_to_keep, :]
  y = y[points_to_keep]


# [1, n_points, k]
y_pred = model(points)

# [n_points]
y_pred = y_pred.argmax(-1).squeeze(0)


plot3d_shapes([points[0], points[0]], [y, y_pred], ['Ground truth', 'Prediction'])

In [ ]:
! pip install meshio

In [ ]:
! git clone 'https://github.com/melzismn/Digital-Design-2020-2021.git'

fatal: destination path 'Digital-Design-2020-2021' already exists and is not an empty directory.


In [ ]:
!ls Digital-Design-2020-2021/data

30.obj	bunny.off     cylinder_rot.pcd	tr_reg_040.off	tr_reg_089.off
3.obj	cylinder.pcd  MooseOBJ.obj	tr_reg_043.off	tr_reg_090.off


In [ ]:
#@title Out of distribution predictions { run: "auto" }

from pathlib import Path
test_shapes = sorted(Path('Digital-Design-2020-2021/data').iterdir())

model.eval()
import meshio

select_shape = 0 #@param {type:"slider", min:0, max:9, step:1}
shape_path = test_shapes[select_shape]

try:
  shape = meshio.read(shape_path).points
except:
  shape = np.loadtxt(shape_path)

points = torch.from_numpy(shape).float()[None, :, :3]


# [1, n_points, k]
y_pred = model(points)

# [n_points]
y_pred = y_pred.argmax(-1).squeeze(0)


plot3d_shapes([points[0]], [y_pred], [f'{shape_path.name}'])